In [10]:
import func.datastruct as ds

ds_zarr = ds.Datastruct()
ds_hdf5 = ds.Datastruct()
ds_netcdf4 = ds.Datastruct()
#new.create(path="data/test_dataset.zarr", shape=(512, 512, 512), chunks=(512, 512, 8), mode="r+", engine="zarr")

ds_zarr.create(path="data/datasets/test_dataset.zarr", shape=(512, 512, 512), chunks=(512, 512, 8), engine="zarr")
ds_hdf5.create(path="data/datasets/test_dataset.h5", shape=(512, 512, 512), chunks=(512, 512, 8), engine="hdf5")
ds_netcdf4.create(path="data/datasets/test_dataset.nc", shape=(512, 512, 512), chunks=(512, 512, 8), engine="netcdf4")



In [1]:
import func.datastruct as ds

ds_zarr = ds.Datastruct()
ds_zarr.open(mode="r+", engine="zarr", path="data/datasets/test_dataset.zarr")

ds_zarr.read("bench_complete", variable="X", iterations=10_000)


pid: 75943
 take some time to set up logger
FINISHED


In [2]:
import func.datastruct as ds

ds_hdf5 = ds.Datastruct()
ds_hdf5.open(mode="r+", engine="hdf5", path="data/datasets/test_dataset.h5")

ds_hdf5.read("bench_complete", variable="X", iterations=10_000)


pid: 75973
 take some time to set up logger
FINISHED


In [3]:
import func.datastruct as ds
    
ds_netcdf4 = ds.Datastruct()
ds_netcdf4.open(mode="r+", engine="netcdf4", path="data/datasets/test_dataset.nc")

ds_netcdf4.read("bench_complete", variable="X", iterations=10_000)

pid: 75986
 take some time to set up logger
FINISHED


In [12]:
import pandas as pd
import numpy as np

df_bench = pd.DataFrame()
df_bench.insert(0, "bench zarr", ds_zarr.log)
df_bench.insert(1, "bench hdf5", ds_hdf5.log)
df_bench.insert(2, "bench netcdf4", ds_netcdf4.log)

def filter_outliers(df) -> pd.DataFrame:
    cols = df.select_dtypes('number').columns
    df_sub = df.loc[:, cols]
    
    iqr = df_sub.quantile(0.75, numeric_only=False) - df_sub.quantile(0.25, numeric_only=False)
    lim = np.abs((df_sub - df_sub.median()) / iqr) < 2.22
    df.loc[:, cols] = df_sub.where(lim, np.nan)
    df.dropna(inplace=True)
    
    return df

if False:
    
    df_bench = filter_outliers(df_bench)

In [13]:
import plotly.express as px

fig = px.box(data_frame=df_bench, log_y=True)
fig.show()

fig = px.violin(data_frame=df_bench)
fig.show()
    
fig = px.histogram(data_frame=df_bench, log_y=True, marginal="violin", barmode="group")
fig.show()

In [ ]:
%%script false --no-raise-error
from mpi4py import MPI
import numpy as np
from netCDF4 import Dataset

rank = MPI.COMM_WORLD.rank
nc = Dataset('parallel_test.nc','w',parallel=True)
d = nc.createDimension('dim',4)
v = nc.createVariable('var', np.int64, 'dim')
v[rank] = rank
nc.close()